<a href="https://colab.research.google.com/github/GuerrSim96/DM_NMR_tfe/blob/main/DM_NMR_tfe.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#MONTARE IL DRIVE DEL PROPRIO ACCOUNT:

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


___
#MONTARE IL DRIVE DI UN ALTRO ACCOUNT:

In [ ]:
# !sudo add-apt-repository -y ppa:alessandro-strada/ppa 2>&1 > /dev/null
# !sudo apt-get update -qq 2>&1 > /dev/null
# !sudo apt -y install -qq google-drive-ocamlfuse 2>&1 > /dev/null
# !google-drive-ocamlfuse

In [ ]:
# !sudo apt-get install -qq w3m # to act as web browser
# !xdg-settings set default-web-browser w3m.desktop # to set default browser
# %cd /content
# !mkdir drive
# %cd drive
# !mkdir MyDrive
# %cd ..
# !google-drive-ocamlfuse /content/drive/MyDrive

#CODICE

In [ ]:
# Install of py3Dmol and biopython
!pip --quiet install biopython  # --quiet flag prevents printing of the output
!pip --quiet install py3Dmol
print('Istallazione di biopython, py3Dmol completata!!!')

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 11.7 MB/s eta 0:00:00
Istallazione di biopython, py3Dmol completata!!!


In [ ]:
# Time when the program begins
import time
from datetime import datetime
time_start = time.time()  # Get the time in seconds
date_time_start = datetime.fromtimestamp(time_start)  # To convert the time by seconds to date and time
with open('timer', 'x') as clk:
  clk.write(f'Start:\t\t{date_time_start}\n')
# Import parameters files
import os
import sys
import shutil as sh
path_mdp='/content/drive/MyDrive/md_files/mdp/'
par= os.listdir(path_mdp)
mdp=['ions.mdp','minim.mdp','nvt.mdp','npt.mdp','md.mdp']
fc=os.listdir('/content')
for p in mdp:
  if p not in par:
    print(f'{p} there is not in {path_mdp}')
    sys.exit  # Block the execution of the code
  else:
    print(p+' is already there')
  if p not in fc:
    sh.copy(path_mdp+p, '/content')  # Copy a file in the working directory
    print(f'-The file \"{p}\" has been moved successfully')
  else:
    print(f'-The file \"{p}\" is already in /content')

ions.mdp is already there
-The file "ions.mdp" has been moved successfully
minim.mdp is already there
-The file "minim.mdp" has been moved successfully
nvt.mdp is already there
-The file "nvt.mdp" has been moved successfully
npt.mdp is already there
-The file "npt.mdp" has been moved successfully
md.mdp is already there
-The file "md.mdp" has been moved successfully


In [ ]:
path_solvs='/content/drive/MyDrive/md_files/input/'
solvs=['trifluoroethanol.pdb', 'tip3p_added.pdb']
for solv in solvs:
  if solv not in fc:
    sh.copy(path_solvs+solv, '/content')  # Copy a file in the working directory
    print(f'-The file \"{solv}\" has been moved successfully')
  else:
    print(f'-The file \"{solv}\" is already in /content')

-The file "trifluoroethanol.pdb" has been moved successfully
-The file "tip3p_added.pdb" has been moved successfully


In [ ]:
#@title ##Get the structure
from Bio.PDB import *
#@markdown Enter the identification code of the pdb structure in the line below:
pdb_id = "6fs5"  #@param {type:"string"}
pdbl= PDBList()
parser= PDBParser(PERMISSIVE=True, QUIET=True)
pdbl.retrieve_pdb_file(pdb_id, pdir='.', file_format ='pdb', overwrite=True)
os.rename(f'pdb{pdb_id.lower()}.ent', f'{pdb_id}.pdb')  # Convert the str id in lowercase
structure = parser.get_structure(pdb_id, f'{pdb_id}.pdb')
model = structure.get_models()
models= list(model)
input_f=models[0]
io= PDBIO()
io.set_structure(input_f)  # Get only one model from a NMR file
io.save("file.pdb")

In [ ]:
import subprocess
path_bin='/content/drive/MyDrive/IBM3202/gromacs-2023/bin/'
os.environ['PATH'] += f':{path_bin}'

In [ ]:
# To understand
for root, directories, files in os.walk(path_bin):
    for dir in directories:
        os.chmod(os.path.join(root, dir), 0o777)
    for f in files:
        os.chmod(os.path.join(root, f), 0o777)
subprocess.Popen('source "$PATH"/GMXRC.bash', shell=True, executable='/bin/bash', stdout=subprocess.PIPE, stderr=subprocess.PIPE)

<Popen: returncode: None args: 'source "$PATH"/GMXRC.bash'>

In [ ]:
def gmx(cmd):
  '''To launch gmx process'''
  process = subprocess.Popen(cmd, shell=True, executable='/bin/bash', stdout=subprocess.PIPE, stderr=subprocess.PIPE)
  output, error = process.communicate()
  print(f'Output: \n{output.decode("utf-8")} \n\nError: \n{error.decode("utf-8")}\n\n')

In [ ]:
# Removing water
!grep -v HOH file.pdb > file_clean.pdb
# Counting the sulfur bond
ss, line= 0, 'y \n'
with open(f'{pdb_id}.pdb', 'r') as pdb:
  for line in pdb:
    if 'SSBOND' in line:
      ss+=1
with open('options', 'x') as file:
  for x in range(ss):
    file.write(line)
# Prepare the topology with oplsaa ff and tip3p water model -ingh is a flag that we can use with a file.pdb generated from an NMR technique
pdb2gmx= 'gmx pdb2gmx -f file_clean.pdb -o file_processed.pdb -water tip3p -ff oplsaa -ignh -ss yes < options'
gmx(pdb2gmx)

Output: 
Using the Oplsaa force field in directory oplsaa.ff

going to rename oplsaa.ff/aminoacids.r2b
Reading file_clean.pdb...
Read '', 344 atoms

Analyzing pdb file
Splitting chemical chains based on TER records or chain id changing.

There are 1 chains and 0 blocks of water and 39 residues with 344 atoms

  chain  #res #atoms

  1 'A'    39    344  

All occupancies are one

Reading residue database... (Oplsaa)

Processing chain 1 'A' (344 atoms, 39 residues)

Identified residue LYS1 as a starting terminus.

Identified residue LYS39 as a ending terminus.
Start terminus LYS-1: NH3+
End terminus LYS-39: COO-

Checking for duplicate atoms....

Generating any missing hydrogen atoms and/or adding termini.

Now there are 39 residues with 712 atoms

Making bonds...

Number of bonds was 718, now 718

Generating angles, dihedrals and pairs...

Making cmap torsions...

There are 1915 dihedrals,  136 impropers, 1304 angles
          1890 pairs,      718 bonds and     0 virtual sites

Total ma

In [ ]:
with open('options', 'w') as file:
   file.write('Backbone \n')
# Orient the structure with the major axis coincident with the x-axis
orient='gmx editconf -f file_processed.pdb -o file_oriented.pdb -princ < options'
gmx(orient)
x,y,z = [],[],[]
with open('file_oriented.pdb', 'r') as protein:
  for line in protein:
    if line.startswith("ATOM"):
      # extract x, y, z coordinates for carbon alpha atoms
      x_c = float(line[30:38].strip())
      y_c = float(line[38:46].strip())
      z_c = float(line[46:54].strip())
      if line[12:16].strip() == "CA":
        x.append(x_c)
        y.append(y_c)
        z.append(z_c)
x_max, x_min= x.index(max(x)), x.index(min(x))
y_max, y_min= y.index(max(y)), y.index(min(y))
z_max, z_min= z.index(max(z)), z.index(min(z))
dist_x=((x[x_min]-x[x_max])**2 + (y[x_min]-y[x_max])**2 + (z[x_min]-z[x_max])**2)**0.5 /10
dist_y=((x[y_min]-x[y_max])**2 + (y[y_min]-y[y_max])**2 + (z[y_min]-z[y_max])**2)**0.5 /10
dist_z=((x[z_min]-x[z_max])**2 + (y[z_min]-y[z_max])**2 + (z[z_min]-z[z_max])**2)**0.5 /10
x_l, y_l, z_l= int(dist_x*1.75)+1, int(dist_y*1.75)+1, int(dist_z*1.75)+1
os.environ['MAIN_AXIS_BOX']= str(x_l) #trasferire una variabile da python a bash
if y_l > z_l:
  os.environ['SEC_AXIS_BOX']= str(y_l)
else:
  os.environ['SEC_AXIS_BOX']= str(z_l)

Output: 
Note that major changes are planned in future for editconf, to improve usability and utility.
Read 712 atoms
No velocities found
    system size :  3.186  5.968  2.424 (nm)
    center      :  0.000  2.596 -1.024 (nm)
    box vectors :  0.000  0.000  0.000 (nm)
    box angles  :   0.00   0.00   0.00 (degrees)
    box volume  :   0.00               (nm^3)

         based on residue and atom names, since they could not be
         definitively assigned from the information in your input
         files. These guessed numbers might deviate from the mass
         and radius of the atom type. Please check the output
         files if necessary. Note, that this functionality may
         be removed in a future GROMACS version. Please, consider
         using another file format for your input.

Selected 4: 'Backbone'
new system size :  6.256  2.254  1.902
new center      : -0.042  2.636 -1.001 (nm)
new box vectors :  0.000  0.000  0.000 (nm)
new box angles  :   0.00   0.00   0.00 (deg

In [ ]:
#@title #####Solvation
# Define the box cell as triclinic and add water using the spc216 equilibrated 3-point solvent model
editconf='gmx editconf -f file_oriented.pdb -o file_newbox.pdb -bt triclinic -c -box "$MAIN_AXIS_BOX" "$SEC_AXIS_BOX" "$SEC_AXIS_BOX"'
solvate='gmx solvate -cp file_newbox.pdb -cs spc216.gro -o file_solv.pdb -p topol.top'
gmx(editconf)
gmx(solvate)

Output: 
Note that major changes are planned in future for editconf, to improve usability and utility.
Read 712 atoms
No velocities found
    system size :  6.256  2.254  1.902 (nm)
    center      : -0.042  2.636 -1.001 (nm)
    box vectors :  0.000  0.000  0.000 (nm)
    box angles  :   0.00   0.00   0.00 (degrees)
    box volume  :   0.00               (nm^3)
    shift       :  5.042  0.864  4.501 (nm)
new center      :  5.000  3.500  3.500 (nm)
new box vectors : 10.000  7.000  7.000 (nm)
new box angles  :  90.00  90.00  90.00 (degrees)
new box volume  : 490.00               (nm^3)
 

Error: 
                      :-) GROMACS - gmx editconf, 2023 (-:

Executable:   /content/drive/MyDrive/IBM3202/gromacs-2023/bin/gmx
Data prefix:  /content/drive/MyDrive/IBM3202/gromacs-2023
Working dir:  /content
Command line:
  gmx editconf -f file_oriented.pdb -o file_newbox.pdb -bt triclinic -c -box 10 7 7


GROMACS reminds you: "Jesus Built My Hotrod" (Ministry)




Output: 

         based on re

In [ ]:
#@title #####Neutralizing the system
!grep 'qtot' topol.top
# Generate the run input for genion
grompp_ions= 'gmx grompp -f ions.mdp -c file_solv.pdb -p topol.top -o ions.tpr -maxwarn 1'
gmx(grompp_ions)
# Overwrite "options" file, it will be used ad imput insed of the std input
with open('options', 'w') as file:
  file.write('SOL \n')
# Replace some water molecules (SOL) with ions to remove net charge
genion= 'gmx genion -s ions.tpr -o file_solv_ions.pdb -p topol.top -pname NA -nname CL -conc 0.15 -neutral < options'
gmx(genion)

    24   opls_236      1    LYS      O      7       -0.5    15.9994   ; qtot 2
    38   opls_236      2    THR      O     11       -0.5    15.9994   ; qtot 2
    60   opls_236      3    LYS      O     18       -0.5    15.9994   ; qtot 3
    79   opls_236      4    LEU      O     24       -0.5    15.9994   ; qtot 3
    93   opls_236      5    THR      O     28       -0.5    15.9994   ; qtot 3
   108   opls_236      6    GLU      O     33       -0.5    15.9994   ; qtot 2
   123   opls_236      7    GLU      O     38       -0.5    15.9994   ; qtot 1
   138   opls_236      8    GLU      O     43       -0.5    15.9994   ; qtot 0
   160   opls_236      9    LYS      O     50       -0.5    15.9994   ; qtot 1
   174   opls_236     10    ASN      O     56       -0.5    15.9994   ; qtot 1
   198   opls_236     11    ARG      O     64       -0.5    15.9994   ; qtot 2
   217   opls_236     12    LEU      O     70       -0.5    15.9994   ; qtot 2
   231   opls_236     13    ASN      O     76       

In [ ]:
#@title # Co-solvation with **trifluoroethanol**
#@markdown If you want **trifluoroethanol** in the system flag the box below:
include_tfe= True #@param {type:'boolean'}
# if statement
if include_tfe: # True
  with open('options', 'w') as file:
    file.write('TFE \n')
  # Produces an #include file for a topology
  restr_tfe= 'gmx genrestr -f trifluoroethanol.pdb -o porse_tfe.itp < options'
  gmx(restr_tfe)
  # Find where insert the string #include file
  with open('topol.top', 'r') as top:
    info= top.readlines()
  with open('topol.top', 'r') as top:
    for num, line in enumerate(top, 1):
      if '#include "oplsaa.ff/ions.itp"' in line:
        t_line= num
  add_info='\n;Include TFE topology \n#include "oplsaa.ff/trifluoroethanol.itp" \n \n;Include Position restraint file \n#ifdef POSRES_TFE \n#include "posre_tfe.itp" \n#endif \n'
  info.insert(t_line, add_info) # Write in topol.top
  with open('topol.top', 'w') as top:
    info= ''.join(info)
    top.write(info)
  # To calculate the molecules number of tfe to add in the simulation box
  from scipy.constants import Avogadro
  with open('topol.top', 'r') as top:
    for line in top:
      if 'SOL' in line:  # To get the number of the water molecules
        field = line.split()  # Divide the row in elements
        for element in field:
          if element.isdigit():  # Verify if the element is a number
            w_n = int(element)  # Convert from str into int
  #@markdown Trifluoroethanol percentage (%v/v):
  tfe_percent= 60 #@param {type:"slider", min:10, max:100, step:10}
  w_percent= 100- tfe_percent
  w_vol_mol, tfe_vol_mol, w_mol= 0.01807, 0.07232, w_n/Avogadro  # Convert in moles
  w_vol, k= w_mol * w_vol_mol, w_vol_mol/tfe_vol_mol
  tfe_vol, w_vol_new= w_vol * tfe_percent/100, w_vol * w_percent/100
  tfe_mol, w_mol_new= tfe_vol / tfe_vol_mol, w_vol_new / w_vol_mol
  tfe_n_i, w_n_new= tfe_mol * Avogadro, w_mol_new * Avogadro
  tfe_n_r= int(tfe_n_i*(1-k))  # Number of trifluorethanol molecules
  os.environ['MOLS_TFE'] = str(tfe_n_r)  # Trasfer variable from python to bash
  with open('options', 'w') as file:  # Change options file
    file.write('SOL \n')
  # Add trifluoroethanol in the system
  insert_tfe= 'gmx insert-molecules -f file_solv_ions.pdb -ci trifluoroethanol.pdb -nmol "$MOLS_TFE" -o file_solv_ions_tfe.pdb -replace < options &> replaced_water'
  gmx(insert_tfe)
  # Modify topology file
  with open('topol.top', 'a') as top:  # Add at the end of the file
    top.write(f'TFE {tfe_n_r} \n')  # Write the number of trifluoroethanol molecules
  with open('replaced_water', 'r') as file:
    for line in file:
      if 'Replaced' in line:
        field = line.split()  # Divide the row in elements
        for element in field:
          if element.isdigit():  # Verify if the element is a number
            w_replaced= int(element)  # Convert from str into int
  diff=w_n-w_replaced-int(w_n_new)
  os.environ['MOL_WATER'] = str(diff)
  # Add water molecules to obrtain the correct proportion between trifluoroethanol and water
  insert_w= 'gmx insert-molecules -f file_solv_ions_tfe.pdb  -ci tip3p_added.pdb -nmol "$MOL_WATER" -o file_solv_ions_tfe_solv.gro &> added_water'
  gmx(insert_w)
  # Verify if water molecules were added
  with open('added_water', 'r') as file:  # Search into the file
    for line in file:
      if 'Added' in line:
        field = line.split()  # Divide the row in elements
        for element in field:
          if element.isdigit():  # Verify if the element is a number
            w_added= int(element)  # Convert from str into int
  if w_added == diff:
    print('All water molecules have been added in the simulation box!')
  else:  # Block the execution of the code
    sys.exit('the condition "w_added == diff" must be true to allow the execution of the code.')
  # Modify topol.top after added water molecules
  w_1, w_2= w_n - w_replaced,  w_n_new + w_added
  if w_1==int(w_2):
    mod_water= w_1
  else:
    w_1+=1
    mod_water= w_1
  with open('topol.top', 'r') as top:  # Search into the file
    info= top.readlines()
  with open('topol.top', 'r') as top:
    for num, line in enumerate(top, 1):
      if 'SOL' in line:
        t_line= num - 1
  info[t_line]=f'SOL {mod_water} \n'
  with open('topol.top', 'w') as top:
    top.writelines(info)
  with open('options', 'w') as file: # Overwrite options file
    file.write('Water \n')
  # Produce an #include file for a topology
  restr_w= 'gmx genrestr -f tip3p_added.pdb -o porse_tip3p_added.itp < options'
  gmx(restr_w)
  # Modify the number of water molecules in topol.top
  with open('topol.top', 'r') as top:
    info= top.readlines()
  with open('topol.top', 'r') as top:
    for num, line in enumerate(top, 1):
      if '#endif' in line:
        t_line= num
  add_info='\n;Include tip3p_added topology \n#include "oplsaa.ff/tip3p_added.itp" \n \n;Include Position restraint file \n#ifdef POSRES_TIP3P_ADDED \n#include "posre_tip3p_added.itp" \n#endif \n'
  info.insert(t_line, add_info)
  with open('topol.top', 'w') as top:
    info= ''.join(info)
    top.write(info)
  with open('topol.top', 'a') as top:
    top.write(f'SOL {w_added} \n')
  # Set the variables for the cell below
  to_screen= 'file_solv_ions_tfe.pdb'
  to_minimize= 'file_solv_ions_tfe_solv.gro'
  os.environ['TO_MINIMIZE']= to_minimize
else: # False
  to_screen= 'file_solv_ions.pdb'
  os.environ['TO_MINIMIZE']= to_screen

Output: 
Select group to position restrain
Selected 2: 'TFE'
 

Error: 
                      :-) GROMACS - gmx genrestr, 2023 (-:

Executable:   /content/drive/MyDrive/IBM3202/gromacs-2023/bin/gmx
Data prefix:  /content/drive/MyDrive/IBM3202/gromacs-2023
Working dir:  /content
Command line:
  gmx genrestr -f trifluoroethanol.pdb -o porse_tfe.itp


Reading structure file
Group     0 (         System) has     9 elements
Group     1 (Trifluoroethanol) has     9 elements
Group     2 (            TFE) has     9 elements
Select a group: 
GROMACS reminds you: "Nurture Another Mind, Before Yours Expires" (Arrested Development)




Output: 
 

Error: 



Output: 
 

Error: 



All water molecules have been added in the simulation box!
Output: 
Select group to position restrain
Selected 1: 'Water'
 

Error: 
                      :-) GROMACS - gmx genrestr, 2023 (-:

Executable:   /content/drive/MyDrive/IBM3202/gromacs-2023/bin/gmx
Data prefix:  /content/drive/MyDrive/IBM3202/gromacs-2023
Worki

In [ ]:
#@title ###Simulation box system
import py3Dmol
view= py3Dmol.view()
view.addModel(open(to_screen, 'r').read(),'pdb')  # File to screen
view.setBackgroundColor('Black')  # Background color
view.addStyle({'atom':'OW'},{'sphere':{'radius':'0.1'}})  # Style water molecules
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
#@title ###Minimization
# Relax the system
grompp_minim, mdrun_minim= 'gmx grompp -f minim.mdp -c "$TO_MINIMIZE" -o em.tpr -maxwarn 1', 'gmx mdrun -deffnm em'
gmx(grompp_minim)
gmx(mdrun_minim)

Output: 
Setting the LD random seed to -786730

Generated 335790 of the 335790 non-bonded parameter combinations

Generated 335790 of the 335790 1-4 parameter combinations

Excluding 3 bonded neighbours molecule type 'Protein_chain_A'

Excluding 2 bonded neighbours molecule type 'SOL'

Excluding 1 bonded neighbours molecule type 'NA'

Excluding 1 bonded neighbours molecule type 'CL'

Excluding 3 bonded neighbours molecule type 'TFE'

Excluding 2 bonded neighbours molecule type 'SOL'

++++ PLEASE READ AND CITE THE FOLLOWING REFERENCE ++++
J. S. Hub, B. L. de Groot, H. Grubmueller, G. Groenhof
Quantifying Artifacts in Ewald Simulations of Inhomogeneous Systems with a Net
Charge
J. Chem. Theory Comput. 10 (2014) pp. 381-393
-------- -------- --- Thank You --- -------- --------

Analysing residue names:
There are:    39    Protein residues
There are:  8255      Water residues
There are:    95        Ion residues
There are:  1768 Trifluoroethanol residues
Analysing Protein...
Analysing resi

In [ ]:
#@title #####Equilibration (nVT)
# Equilibration phase I (under nVT/isothermal-isochoric/canonical) - stabilizes T
grompp_nvt, mdrun_nvt= 'gmx grompp -v -f nvt.mdp -c em.gro -r em.gro -p topol.top -o nvt.tpr -maxwarn 1', 'gmx mdrun -deffnm nvt'
gmx(grompp_nvt)
gmx(mdrun_nvt)

Output: 
checking input for internal consistency...

Setting the LD random seed to -1376074013

processing topology...

Generated 335790 of the 335790 non-bonded parameter combinations

Generated 335790 of the 335790 1-4 parameter combinations

Excluding 3 bonded neighbours molecule type 'Protein_chain_A'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

turning H bonds into constraints...

Excluding 1 bonded neighbours molecule type 'NA'

turning H bonds into constraints...

Excluding 1 bonded neighbours molecule type 'CL'

turning H bonds into constraints...

Excluding 3 bonded neighbours molecule type 'TFE'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

++++ PLEASE READ AND CITE THE FOLLOWING REFERENCE ++++
J. S. Hub, B. L. de Groot, H. Grubmueller, G. Groenhof
Quantifying Artifacts in Ewald Simulations of Inhomogeneous Systems with a Net
Charge
J. Chem. Theory Comput. 10 (2014) pp. 381-393
-------- ---

In [ ]:
#@title #####Equilibration (npT)
# Equilibration phase II (under npT/isothermal-isobaric) - stabilizes p
grompp_npt, mdrun_npt= 'gmx grompp -f npt.mdp -c nvt.gro -r nvt.gro -t nvt.cpt -p topol.top -o npt.tpr -maxwarn 2', 'gmx mdrun -deffnm npt'
gmx(grompp_npt)
gmx(mdrun_npt)

Output: 
Setting the LD random seed to 1585165754

Generated 335790 of the 335790 non-bonded parameter combinations

Generated 335790 of the 335790 1-4 parameter combinations

Excluding 3 bonded neighbours molecule type 'Protein_chain_A'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

turning H bonds into constraints...

Excluding 1 bonded neighbours molecule type 'NA'

turning H bonds into constraints...

Excluding 1 bonded neighbours molecule type 'CL'

turning H bonds into constraints...

Excluding 3 bonded neighbours molecule type 'TFE'

turning H bonds into constraints...

Excluding 2 bonded neighbours molecule type 'SOL'

++++ PLEASE READ AND CITE THE FOLLOWING REFERENCE ++++
J. S. Hub, B. L. de Groot, H. Grubmueller, G. Groenhof
Quantifying Artifacts in Ewald Simulations of Inhomogeneous Systems with a Net
Charge
J. Chem. Theory Comput. 10 (2014) pp. 381-393
-------- -------- --- Thank You --- -------- --------


The center of mass of the

In [ ]:
def pa_di(list_path):
  '''Function to create new directory into the drive, starting from a list of names.'''
  print(pa_di.__doc__)
  for dir in list_path:
    if os.path.isdir(dir) is True:
      print('-The directory \"'+ dir +'\" is already there')
    else:
      os.mkdir(dir)
      print('-The directory \"'+ dir +'\" has been created successfully')

In [ ]:
lst_dir, path_simul= [], f'/content/drive/MyDrive/md_files/{pdb_id}'
lst_dir.append(path_simul)
path_par = path_simul + '/parameters/' # Subdirectory to separate the outputs
lst_dir.append(path_par)
pa_di(lst_dir)
here= os.getcwd()
os.environ['DIRECTORY'] = '/content/'
if here != path_simul:
  os.chdir(path_simul)
  print(f'\n-Now the working directory is \"{path_simul}\"')
else:
  print(f'\n-The working directory was already \"{path_simul}\"')

Function to create new directory into the drive, starting from a list of names.
-The directory "/content/drive/MyDrive/md_files/6fs5" is already there
-The directory "/content/drive/MyDrive/md_files/6fs5/parameters/" is already there

-Now the working directory is "/content/drive/MyDrive/md_files/6fs5"


In [ ]:
# Assemble the structure for a 10-ns MD simulation using md.mdp as a parameter file
gromp_md= 'gmx grompp -f "$DIRECTORY"md.mdp -c "$DIRECTORY"npt.gro -t "$DIRECTORY"npt.cpt -p "$DIRECTORY"topol.top -o md_1.tpr -maxwarn 1'
gmx(gromp_md)

Output: 
 

Error: 
                       :-) GROMACS - gmx grompp, 2023 (-:

Executable:   /content/drive/MyDrive/IBM3202/gromacs-2023/bin/gmx
Data prefix:  /content/drive/MyDrive/IBM3202/gromacs-2023
Working dir:  /content/drive/MyDrive/md_files/6fs5
Command line:
  gmx grompp -f /content/md.mdp -c /content/npt.gro -t /content/npt.cpt -p /content/topol.top -o md_1.tpr -maxwarn 1


-------------------------------------------------------
Program:     gmx grompp, version 2023
Source file: src/gromacs/commandline/cmdlineparser.cpp (line 271)
Function:    void gmx::CommandLineParser::parse(int*, char**)

Error in user input:
Invalid command-line options
  In command-line option -c
    File '/content/npt.gro' does not exist or is not accessible.
    The file could not be opened.
      Reason: No such file or directory
      (call to fopen() returned error code 2)
  In command-line option -t
    File '/content/npt.cpt' does not exist or is not accessible.
    The file could not be opened.


In [ ]:
fc_1, files_par, files_simul= os.listdir('/content'), os.listdir(path_par), os.listdir(path_simul)
for file in fc_1:
  if file.endswith('.top'):
    if file not in files_simul:
      sh.copy(f'/content/{file}', path_simul)
      print(f'-The file \"{file}\" has been moved successfully')
    else:
      print(f'-The file \"{file}\" is already there'.upper()) # It will be printed in UPPERCASE
  elif file.endswith('.mdp'):
    if file not in files_par:
      sh.copy(f'/content/{file}', path_par)
      print(f'-The file \"{file}\" has been moved successfully')
    else:
      print(f'-The file \"{file}\" is already there')

-THE FILE "TOPOL.TOP" IS ALREADY THERE
-The file "mdout.mdp" is already there
-The file "md.mdp" is already there
-The file "nvt.mdp" is already there
-The file "minim.mdp" is already there
-The file "ions.mdp" is already there
-The file "npt.mdp" is already there


#Molecular dynamics simulation

In [ ]:
#@title #####First 10ns simulation
# Time when molecular dynamics begins
time_md_s= time.time()
date_time_md_s= datetime.fromtimestamp(time_md_s) # To convert the time by seconds to date and time
with open('timer', 'a') as clk:
  clk.write(f'MD start:\t{date_time_md_s}\n')
# Run the 10ns MD simulation
mdrun_md= 'gmx mdrun -deffnm md_1'
gmx(mdrun_md)
# Time when the first simulation ends
time_md_e= time.time()
date_time_md_e= datetime.fromtimestamp(time_md_e) # To convert the time by seconds to date and time
with open('timer', 'a') as clk:
  clk.write(f'MD 10ns:\t\t{date_time_md_e}\n')

NameError: ignored

In [ ]:
#@title #####Other 10ns simulation
# Extend the simulation for 10ns
extend, mdrun_extend= 'gmx convert-tpr -s md_1.tpr -extend 10000 -o md_2.tpr', 'gmx mdrun -deffnm md_2 -cpi md_1.cpt -noappend'
gmx(extend)
gmx(mdrun_extend)
# Time when the second simulation ends
time_end= time.time()
date_time_end= datetime.fromtimestamp(time_end) # To convert the time by seconds to date and time
with open('timer', 'a') as clk:
  clk.write(f'MD 20ns:\t\t\t{date_time_end}\n')

In [ ]:
# Merge the trajectories
merge= 'gmx trjcat -f md*.xtc -o md_20ns.xtc'
gmx(merge)
with open('options', 'w') as file:
  file.write('Protein \n System \n')
# Puts the center of mass of molecules in the box
trjconv= 'gmx trjconv -s md_2.tpr -f md_20ns.xtc -o md_20ns_protPBC.xtc -pbc mol -center < options'
gmx(trjconv)
# Time when the program ends
time_end= time.time()
date_time_end= datetime.fromtimestamp(time_end) # To convert the time by seconds to date and time
with open('timer', 'a') as clk:
  clk.write(f'End:\t\t\t{date_time_end}\n')